In [337]:
import numpy as np
import matplotlib.pyplot as plt

In [338]:
from loaders import clean_text_for_pattern_letter
from temp_text_puh import template_str
# input_str = clean_text_for_pattern_letter(template_str, out_len=len(template_str))
input_str = clean_text_for_pattern_letter(template_str, out_len=5000)
print(len(input_str))
letters = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u',
               'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', '\'', '1']
print(f'{letters=}')

len(letters)=32
5000
letters=['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', "'", '1']


In [339]:
def predict_train(input_str,
                  letters,
                  max_history=4,
                  max_index: int = 4,):
    WIN: dict[str, dict[str, int]] = {}

    HistoryHW: list[dict[str, int]] = []
    HistoryW: list[dict[str, dict[str, dict[int, int]]]] = []

    for h_idx in range(max_history):
        HistoryHW.append({})
        HistoryW.append({})

    IDX: list = []

    for letter in letters:
        WIN.setdefault(letter, {})

        for idx in range(max_index):
            WIN[letter].setdefault(idx, 0)

    prev_indices = [0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0:
            WIN[inp][prev_indices[0]] += 1
            continue

        IDX.append(prev_indices[0])

        IdxO = {}

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            HW = HistoryHW[h_idx]
            W = HistoryW[h_idx]

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            if HW.get(key_HW, -1) != -1:
                inp_has_index = HW[key_HW]

                # idx_strength = W[prev_inp + str(prev_indices[h_idx])][inp][inp_has_index]

                IdxO.setdefault(inp_has_index, 0)
                IdxO[inp_has_index] += 1

        new_index = 0
        if len(IdxO) == 0:
            new_index = min(WIN[inp], key=WIN[inp].get)
        else:
            new_index = max(IdxO, key=IdxO.get)
        WIN[inp][new_index] += 1

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            key_I = prev_inp + str(prev_indices[h_idx])
            HistoryW[h_idx].setdefault(key_I, {})
            HistoryW[h_idx][key_I].setdefault(inp, {})
            HistoryW[h_idx][key_I][inp].setdefault(new_index, 0)

            stats = HistoryW[h_idx][key_I][inp][new_index]
            if stats == 0:
                HistoryW[h_idx][key_I][inp][new_index] += 1
            else:
                HistoryW[h_idx][key_I][inp][new_index] += 1 / (32 * stats)

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            HistoryHW[h_idx].setdefault(key_HW, new_index)

        # recurtion
        prev_indices.insert(0, new_index)
        if len(prev_indices) > max_history:
            prev_indices = prev_indices[:-1]

    return HistoryW, HistoryHW, IDX

max_index_L1 = 32
max_history_L1 = 12

max_history_L1_ds = 11

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1, max_index=max_index_L1)

for h_idx in range(max_history_L1):
    print(f'{h_idx=}')
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)


h_idx=0
c0 {'h': {0: 1}}
h0 {'a': {0: 1}}
a0 {'p': {0: 1}}
p0 {'t': {0: 1}}
t0 {'e': {0: 1}}
e0 {'r': {0: 1.03125}}
r0 {' ': {0: 1}, 'h': {4: 1}}
 0 {'i': {0: 1}, 'b': {7: 1}, 't': {19: 1}}
i0 {'n': {0: 1}}
n0 {' ': {1: 1}}
 1 {'w': {0: 1}, 'c': {5: 1}, 'o': {24: 1}}
w0 {'h': {1: 1}}
h1 {'i': {1: 1}, 'r': {8: 1}}
i1 {'c': {1: 1}}
c1 {'h': {2: 1}}
h2 {' ': {2: 1}}
 2 {'w': {1: 1}, 'r': {9: 1}, 'i': {12: 1}}
w1 {'e': {1: 1}}
e1 {' ': {3: 1}, 'r': {17: 1}}
 3 {'a': {1: 1.03125}, 'i': {14: 1}}
a1 {'r': {1: 1}, 'n': {12: 1}}
r1 {'e': {2: 1}, ' ': {2: 1}}
e2 {' ': {4: 1.03125}}
 4 {'i': {2: 1.03125}, 't': {9: 1}, 'h': {23: 1}}
i2 {'n': {1: 1}, 's': {9: 1}}
n1 {'t': {1: 1}}
t1 {'r': {2: 1}}
r2 {'o': {0: 1}}
o0 {'d': {0: 1}}
d0 {'u': {0: 1}}
u0 {'c': {2: 1}}
c2 {'e': {3: 1}}
e3 {'d': {1: 1}, 'a': {22: 1}}
d1 {' ': {5: 1}}
 5 {'t': {2: 1}, 'a': {9: 1}, 'h': {19: 1}, 'i': {5: 1}}
t2 {'o': {1: 1}}
o1 {' ': {6: 1}}
 6 {'w': {2: 1}, 'f': {1: 1.03125}, 'a': {20: 1}}
w2 {'i': {3: 1}}
i3 {'n': {2: 1}}

In [340]:
def to_probability(HistoryW: list[dict[str, dict[str, dict[int, int]]]], max_history: int):
    for h_idx in range(max_history):
        W = HistoryW[h_idx]

        for inp_symbol, s_indeces in W.items():
            symbol_stat_sum = 0

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    symbol_stat_sum += idx_stat

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    W[inp_symbol][out_symbol][index] = idx_stat / symbol_stat_sum
    
    return HistoryW
        
HistoryW = to_probability(HistoryW, max_history=max_history_L1)

for h_idx in range(max_history_L1):
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)

c0 {'h': {0: 1.0}}
h0 {'a': {0: 1.0}}
a0 {'p': {0: 1.0}}
p0 {'t': {0: 1.0}}
t0 {'e': {0: 1.0}}
e0 {'r': {0: 1.0}}
r0 {' ': {0: 0.5}, 'h': {4: 0.5}}
 0 {'i': {0: 0.3333333333333333}, 'b': {7: 0.3333333333333333}, 't': {19: 0.3333333333333333}}
i0 {'n': {0: 1.0}}
n0 {' ': {1: 1.0}}
 1 {'w': {0: 0.3333333333333333}, 'c': {5: 0.3333333333333333}, 'o': {24: 0.3333333333333333}}
w0 {'h': {1: 1.0}}
h1 {'i': {1: 0.5}, 'r': {8: 0.5}}
i1 {'c': {1: 1.0}}
c1 {'h': {2: 1.0}}
h2 {' ': {2: 1.0}}
 2 {'w': {1: 0.3333333333333333}, 'r': {9: 0.3333333333333333}, 'i': {12: 0.3333333333333333}}
w1 {'e': {1: 1.0}}
e1 {' ': {3: 0.5}, 'r': {17: 0.5}}
 3 {'a': {1: 0.5076923076923077}, 'i': {14: 0.49230769230769234}}
a1 {'r': {1: 0.5}, 'n': {12: 0.5}}
r1 {'e': {2: 0.5}, ' ': {2: 0.5}}
e2 {' ': {4: 1.0}}
 4 {'i': {2: 0.3402061855670103}, 't': {9: 0.32989690721649484}, 'h': {23: 0.32989690721649484}}
i2 {'n': {1: 0.5}, 's': {9: 0.5}}
n1 {'t': {1: 1.0}}
t1 {'r': {2: 1.0}}
r2 {'o': {0: 1.0}}
o0 {'d': {0: 1.0}}
d0 {

In [341]:
def predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []
    AL = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}
        HO_cnt: dict[str, dict[int, int]] = {}

        itr_max_history = 0

        for h_idx in range(max_history):
            # print(f'{h_idx=}')

            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break

            itr_max_history += 1
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                HO_cnt.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)
                    HO_cnt[key_O].setdefault(key_index, 0)

                    discont = (max_history - h_idx)
                    # discont = pow(0.1, h_idx)
                    # discont = pow(2, (max_history - h_idx))

                    HO[key_O][key_index] += val_index * discont
                    HO_cnt[key_O][key_index] += 1

        # print(f'{HO=}')
        # print(f'{HO_cnt=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        max_arr = []
        for v in HO.values():
            col_max = max(v, key=v.get)
            max_arr.append(col_max)
        
        max_arr = np.array(max_arr)
        # tf = np.mean(np.abs(max_arr - max_arr[np.newaxis].T))

        tf = length
        # tf = len(HO)

        TF.append(tf)

        # max by cnt
        # max_symbol = 'a'
        # max_symbol_index = 0
        # max_val = 0
        # for key, val in HO_cnt.items():
        #     max_idx = max(val, key=val.get)
        #     # HO_cnt[key] = {max_idx: val[max_idx]}

        #     if val[max_idx] > max_val: # 
        #         max_val = val[max_idx]
        #         max_symbol_index = max_idx
        #         max_symbol = key
        # print(f'{max_symbol=}')
        # max by val
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        # win_cnt = 0
        for key, val in HO.items():
            for index, index_stat in val.items():
                index_cnt = HO_cnt[key][index]
                stat = pow(0.7, (itr_max_history - index_cnt)) * index_stat
                # stat = -0.1 * (itr_max_history - index_cnt) + index_stat

                HO[key][index] = stat

            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}

            # max_cnt = HO_cnt[key][max_idx]

            if val[max_idx] > max_val: # and max_cnt >= max_his:
                # print(f'{key=} {val[max_idx]=} {max_cnt=}')
                max_val = val[max_idx]
                max_symbol_index = max_idx
                max_symbol = key
                # win_cnt = max_cnt

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {max_val=} {itr_max_history=} {HO=}', max_symbol_index, max_val)
        # print('')

        # anomaly
        if max_symbol == next_inp:
            AL.append(0)
        else:
            ni_v = HO.get(next_inp, 0)
            if ni_v == 0:
                AL.append(100)
            else:
                max_ni = max(ni_v, key=ni_v.get)
                AL.append(abs(ni_v[max_ni] - max_val))

        new_indices = [max_symbol_index]

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    TF.append(0)
    AL.append(0)
    return err, TF, AL

err_L1, TF_L1, AL_L1 = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)
# err_L1, TF_L1_no, AL_L1_no = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)

print(err_L1, err_L1 / (len(input_str) / 100))

max_symbol='h' next_inp='h' max_val=12.0 itr_max_history=1 HO={'h': {0: 12.0}, 'e': {3: 12.0}, 'o': {15: 12.0}, 'a': {15: 6.086877828054298}, 'k': {0: 12.0}, 'r': {14: 1.9242084235393704}, 'i': {18: 1.4400806252601273}, 'l': {3: 1.4025005786249438}} 0 12.0
max_symbol='a' next_inp='a' max_val=23.0 itr_max_history=2 HO={'a': {0: 23.0}, ' ': {2: 7.699999999999999}, 'd': {1: 7.699999999999999}, 'm': {5: 7.699999999999999}, 'l': {7: 0.8277034598486884}, 'u': {5: 7.699999999999999}, 'e': {15: 0.8277034598486884}, 'r': {8: 7.699999999999999}, 'i': {8: 1.0680946942146976}, 'n': {29: 2.5666666666666664}, 'f': {8: 0.6830977535759072}} 0 23.0
max_symbol='p' next_inp='p' max_val=33.0 itr_max_history=3 HO={'p': {0: 33.0}, 'w': {1: 4.8999999999999995}, ' ': {5: 4.8999999999999995}, 'i': {12: 4.8999999999999995}, 'l': {5: 4.8999999999999995}, 'e': {15: 0.41279331567469874}, 'c': {3: 0.6799862903033801}, 'o': {10: 4.8999999999999995}, 'b': {2: 0.3044839355066493}, 'y': {10: 0.41279331567469874}, 's': 

In [342]:
def get_word_stats(input_str: str | list, TF: list, threshold=0.0):
    buffer: list = [input_str[0]]
    WordStats: dict[str, int] = {}
    WordIndex: dict[str, int] = {}
    next_wrd_idx = 0

    NextLayerOut = []
    DownstreamIndex = {}

    prev_tf = TF[0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0 and inp_idx >= len(input_str) - 1:
            continue

        # if TF[inp_idx] - prev_tf > 0.0: # and abs(TF[inp_idx] - prev_tf) > 0.2:
        # and TF[inp_idx] > threshold:
        if TF[inp_idx] > prev_tf and TF[inp_idx] > TF[inp_idx + 1]:
            word = ''.join(buffer)

            WordStats.setdefault(word, 0)
            WordStats[word] += 1

            if not WordIndex.get(word):
                WordIndex.setdefault(word, next_wrd_idx)
                next_wrd_idx += 1

            wrd_idx = WordIndex.get(word)
            # NextLayerOut.append(str(wrd_idx))
            NextLayerOut.append(word)

            DownstreamIndex.setdefault(inp_idx, 1)

            buffer = [inp]
            prev_tf = TF[inp_idx]

            continue

        TF[inp_idx] = 0

        buffer.append(inp)
        prev_tf = TF[inp_idx]

    # sort
    WordStats = dict(sorted(WordStats.items(), key=lambda item: item[1], reverse=True))

    NextLayerOut.append(str(next_wrd_idx))
    return WordStats, WordIndex, NextLayerOut, DownstreamIndex


TF_L1 = np.array(TF_L1, dtype='float64')
AL_L1 = np.array(AL_L1, dtype='float64')
TF_L1 /= np.max(TF_L1)
AL_L1 /= np.max(AL_L1)
TF_L1 += AL_L1

TF_max_coef = 0.4

# TF_L1[np.where(TF_L1 < np.mean(TF_L1))] = 0
# TF_1 = TF_L1 - np.pad(TF_L1, (1, 0))[:-1]
# TF_2 = TF_L1 - np.pad(TF_L1, (0, 1))[1:]
# TF_L1 = TF_1 + TF_2

# TF_L1[np.where(TF_L1 < 0)] = 0
# TF_L1[np.where(TF_L1 < TF_max_coef)] = 0
TF_L1 = TF_L1.tolist()

WordStats_L1, WordIndex_L1, NextLayerOut_L1, DownstreamIndex_L1 = get_word_stats(input_str=input_str,
                                                                                 TF=TF_L1, 
                                                                                 threshold=0.0, )
print(len(WordStats_L1))
mean_WS = np.mean(np.array(list(WordStats_L1.values())))
print(f'{mean_WS=}')
WS_len = 0
for key, val in WordStats_L1.items():
    # if len(key.strip()) > 1 and val >= mean_WS:
    if val >= mean_WS:
        WS_len += 1
    print(key, val)
print(f'{WS_len=}')

print(f'{NextLayerOut_L1=}')
print(f'{len(NextLayerOut_L1)=}')

print(f'{WordIndex_L1=}')

print(f'{DownstreamIndex_L1=}')


763
mean_WS=2.386631716906946
th 37
 a 33
 t 31
 s 31
 b 28
 h 28
 c 24
e  21
in 20
 w 18
he 17
is 16
nd 16
er 15
st 15
 i 14
as 14
en 13
t  13
aid 13
g  13
an 12
 l 12
at 11
 y 11
ou 10
 f 10
ng 10
he  9
on 9
 p 9
 g 9
id 9
it 9
ed 8
 th 8
 r 8
s  8
or 8
of 8
uzz 8
at  8
do 7
ea 7
to 7
es 7
et 7
 po 7
oh 7
nd  7
ad 7
the 7
el 7
 n 6
ow 6
hr 6
om 6
o  6
 d 6
 m 6
 he 6
hri 6
op 6
d  6
 he  6
ing 6
if 6
ere 5
ing  5
wh 5
re 5
bin 5
 yo 5
ns  5
ik 5
es  5
rs 5
ime 5
ed  5
 o 5
the  5
all 5
we 4
ie  4
ly 4
hat 4
me 4
sa 4
 do 4
ut 4
ha 4
 i  4
 be 4
ee  4
ll 4
 to  4
ee 4
hi 4
nk 4
and 4
be 4
no 4
tt 4
r r 4
ob 4
 to 4
oo 4
ome 3
wa 3
ng  3
bu 3
as  3
 of 3
 of  3
tr 3
you 3
 wi 3
d h 3
 j 3
ht  3
er ro 3
ooh 3
ai 3
ec 3
is  3
all  3
ns 3
ly  3
 li 3
y  3
r ro 3
elf 3
 ve 3
ry 3
 sa 3
 so 3
out  3
un 3
de 3
rs  3
 it 3
gr 3
ne  3
f  3
of  3
t t 3
ot 3
noise 3
ge 3
aki 3
on  3
ust 3
e s 3
and  3
ch 3
 bra 3
rn 3
omi 2
ar  2
 is 2
 the  2
od 2
nn 2
ar 2
us 2
to s 2
ay  2
but 2
ug 2
ph 2
n' 

In [343]:
def downstream_train(input: list, next_layer_out: list, downstream_index: dict[int, int]):
    DSStats = {}

    ds_idx = 1
    ds_inp = next_layer_out[0]

    for inp_idx, inp in enumerate(input[:-1]):
        has_ds_input = downstream_index.get(inp_idx)
        if has_ds_input:
            ds_inp = next_layer_out[ds_idx]
            ds_idx += 1

        ds_key = ds_inp + ':' + inp
        DSStats.setdefault(ds_key, 0)
        DSStats[ds_key] += 1

    return DSStats


DSStats = downstream_train(input=input_str,
                           next_layer_out=NextLayerOut_L1,
                           downstream_index=DownstreamIndex_L1,)

for wk, wv in DSStats.items():
    print(wk, wv)

cch:c 1
cch:h 1
apte:a 1
apte:p 1
apte:t 1
apte:e 1
r in :r 1
r in :  2
r in :i 1
r in :n 1
whi:w 1
whi:h 1
whi:i 1
ch :c 1
ch :h 1
ch :  1
we:w 4
we:e 4
 a:  33
 a:a 33
re :r 1
re :e 1
re :  1
in:i 20
in:n 20
tro:t 1
tro:r 1
tro:o 1
duc:d 1
duc:u 1
duc:c 1
ed:e 8
ed:d 8
 to winn:  2
 to winn:t 1
 to winn:o 1
 to winn:w 1
 to winn:i 1
 to winn:n 2
ie :i 4
ie :e 4
ie :  4
the p:t 1
the p:h 1
the p:e 1
the p:  1
the p:p 1
ooh a:o 2
ooh a:h 1
ooh a:  1
ooh a:a 1
nd s:n 1
nd s:d 1
nd s:  1
nd s:s 1
ome:o 3
ome:m 3
ome:e 3
 bees:  1
 bees:b 1
 bees:e 2
 bees:s 1
 and :  2
 and :a 1
 and :n 1
 and :d 1
the st:t 2
the st:h 1
the st:e 1
the st:  1
the st:s 1
ories:o 1
ories:r 1
ories:i 1
ories:e 1
ories:s 1
 begi:  1
 begi:b 1
 begi:e 1
 begi:g 1
 begi:i 1
n h:n 1
n h:  1
n h:h 1
ere:e 10
ere:r 5
 is ed:  2
 is ed:i 1
 is ed:s 1
 is ed:e 1
 is ed:d 1
wa:w 3
wa:a 3
rd bear:r 2
rd bear:d 1
rd bear:  1
rd bear:b 1
rd bear:e 1
rd bear:a 1
 c:  24
 c:c 24
omi:o 2
omi:m 2
omi:i 2
ng :n 3
ng :g 3
ng 

In [344]:
def downstream_predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            upstream_inp: dict[int, list],
            DSStats: dict[str, int],
            ds_input: list,
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    ds_idx = 1
    ds_inp = ds_input[0]

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}

        for h_idx in range(max_history):
            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            # print(f'{key_I=}')
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)
                # print(f'{key_I=}')

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)

                    HO[key_O][key_index] += val_index

        # print(f'{HO=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        # tf = length
        tf = len(HO)

        TF.append(tf)

        # ds input
        has_ds_input = upstream_inp.get(input_idx + 1)
        if has_ds_input:
            ds_inp = ds_input[ds_idx]
            ds_idx += 1

        # max symbol
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        for key, val in HO.items():
            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}
            max_idx_val = val[max_idx]

            # ds predict
            ds_key = ds_inp + ':' + key
            ds_stats = DSStats.get(ds_key)
            # if ds_stats:
            #     max_idx_val += ds_stats

            if max_idx_val > max_val and ds_stats:
                max_val = max_idx_val
                max_symbol_index = max_idx
                max_symbol = key

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {ds_inp=} {HO=}', max_symbol_index, max_val)

        # print(f'{O.get(max_symbol).keys()=}')
        new_indices = [max_symbol_index]

        if O.get(max_symbol):
            new_indices = list(O.get(max_symbol).keys())            

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    return err, TF

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1_ds, max_index=max_index_L1)

# for h_idx in range(max_history_L1_ds):
#     print(f'{h_idx=}')
#     for wk, wv in HistoryW[h_idx].items():
#         print(wk, wv)

err_L1_ds, TF_L1_ds = downstream_predict(input_str=input_str, 
                                        HistoryW=HistoryW, 
                                        upstream_inp=DownstreamIndex_L1,
                                        DSStats=DSStats,
                                        ds_input=NextLayerOut_L1,
                                        max_history=max_history_L1_ds,
                                        max_index=max_index_L1, )

print(f'{err_L1=}', err_L1 / (len(input_str) / 100))
print(f'{err_L1_ds=}', err_L1_ds / (len(input_str) / 100))

max_symbol='h' next_inp='h' ds_inp='cch' HO={'h': {29: 1.0909910320871516}, 'e': {4: 1.0615530303030303}, 'a': {27: 1.03125}, 'o': {15: 1.0909910320871516}, 'k': {4: 1.0615530303030303}, 'r': {30: 1}, 'l': {4: 1.0615530303030303}, 'i': {22: 1}} 29 1.0909910320871516
max_symbol='e' next_inp='a' ds_inp='apte' HO={'a': {0: 2}, 'o': {2: 1.0615530303030303}, 'e': {9: 2.34980971512213}, ' ': {13: 2.03125}, 'i': {9: 2.0928030303030303}, 't': {8: 1.0615530303030303}, 'r': {26: 2.206027635959888}, 'y': {25: 1}, 'd': {1: 1}, 'n': {24: 1}, 'm': {5: 1.0615530303030303}, 'u': {14: 1.03125}, 'l': {9: 1.0615530303030303}, 'f': {0: 1}} 9 2.34980971512213
max_symbol='p' next_inp='p' ds_inp='apte' HO={'p': {0: 3.03125}, 't': {24: 2.2273902022056227}, 'i': {2: 2.0625}, 'n': {15: 1.1747776359598883}, ' ': {16: 2.0615530303030303}, 's': {31: 2.1787956027178206}, 'w': {1: 2}, "'": {2: 1}, 'y': {19: 2}, 'u': {13: 1}, 'd': {13: 1.0615530303030303}, 'r': {25: 1.2528507280790113}, 'c': {10: 2}, 'a': {1: 2}, 'v'